In [ ]:
import torch
print(torch.__version__)

In [ ]:
import torchvision
print(torchvision.__version__)

In [ ]:
import os, time

import numpy as np
import matplotlib.pylab as plt

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch import optim
import torchvision
from torchvision.transforms import v2
from torchvision import datasets

plt.rcParams['figure.figsize'] = (10, 6)

In [ ]:
torch.cuda.is_available()

# Classification MNIST-Fashion

De nombreux datasets sont accessibles directement: voir
<https://pytorch.org/docs/stable/torchvision/datasets.html>

PyTorch utilise une classe DataLoader qui permet de gérer l’accès aux
données (en particulier, en gérant efficamenet le parallélisme et les
batchs): voir
<https://pytorch.org/docs/stable/data.html#torch.utils.data.DataLoader>

De plus, de nombreuses tranformations sont disponbiles pour réaliser
l’augmentation des données: voir
<https://pytorch.org/docs/stable/torchvision/transforms.html>

On charge ici un dataset prédéfini
<https://pytorch.org/docs/stable/torchvision/datasets.html#torchvision.datasets.FashionMNIST>

Il s’agit de la base d’images décrite ici:
<https://github.com/zalandoresearch/fashion-mnist>

In [ ]:
train_loader = torch.utils.data.DataLoader(
    torchvision.datasets.FashionMNIST('fashionmnist', train=True, download=True,
                   transform=torchvision.transforms.Compose([
                       torchvision.transforms.ToTensor(),
                       torchvision.transforms.Normalize((0.1307,), (0.3081,))
                       ])),
    batch_size=64, shuffle=True)
test_loader = torch.utils.data.DataLoader(
    torchvision.datasets.FashionMNIST('fashionmnist', train=False,
                               transform=torchvision.transforms.Compose([
                                   torchvision.transforms.ToTensor(),
                                   torchvision.transforms.Normalize((0.1307,), (0.3081,))
                                   ])),
    batch_size=1000, shuffle=True)

In [ ]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.conv1 = nn.Conv2d(1, 10, kernel_size=5)
        self.conv2 = nn.Conv2d(10, 20, kernel_size=5)
        self.conv2_drop = nn.Dropout2d()
        self.fc1 = nn.Linear(320, 50)
        self.fc2 = nn.Linear(50, 10)

    def forward(self, x):
        x = F.relu(F.max_pool2d(self.conv1(x), 2))
        x = F.relu(F.max_pool2d(self.conv2_drop(self.conv2(x)), 2))
        x = x.view(-1, 320)
        x = F.relu(self.fc1(x))
        x = F.dropout(x, training=self.training)
        x = self.fc2(x)

        return F.log_softmax(x, dim=1)

In [ ]:
model = Net()

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
model = model.to(device)

Optimizer :
<https://pytorch.org/docs/stable/optim.html#module-torch.optim>

In [ ]:
optimizer = optim.SGD(model.parameters(), lr=0.01)

Fonction de loss
<https://pytorch.org/docs/stable/nn.html#loss-functions>

In [ ]:
criterion = torch.nn.NLLLoss()

Fonction de train:

In [ ]:
def train(model, device, train_loader, optimizer, epoch, criterion):
    model.train()
    for batch_idx, (data, target) in enumerate(train_loader):
        data, target = data.to(device), target.to(device)
        optimizer.zero_grad()

        output = model(data)
        loss = criterion(output, target)
        loss.backward()
        optimizer.step()
        
        if batch_idx % 100 == 0:
            print('Train Epoch: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}'.format(
                epoch, batch_idx * len(data), len(train_loader.dataset),
                100. * batch_idx / len(train_loader), loss.item()))

Fonction de test:

In [ ]:
def test(model, device, test_loader, criterion):
    model.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        for data, target in test_loader:
            data, target = data.to(device), target.to(device)
            output = model(data)
            test_loss += criterion(output, target).item() # sum up batch loss
            pred = output.max(1, keepdim=True)[1] # get the index of the max log-probability
            correct += pred.eq(target.view_as(pred)).sum().item()

    test_loss /= len(test_loader.dataset)
    print('\nTest set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        test_loss, correct, len(test_loader.dataset),
        100. * correct / len(test_loader.dataset)))
    return 

In [ ]:
for epoch in range(1, 10):
        start_time = time.process_time()
        train(model, device, train_loader, optimizer, epoch,criterion)
        end_time = time.process_time()
        print("Train Epoch duration {:.2f}s".format(end_time - start_time))
        
        test(model, device, test_loader,criterion)

    Train Epoch: 1 [0/60000 (0%)]   Loss: 2.331967
    Train Epoch: 1 [6400/60000 (11%)]   Loss: 2.220635
    Train Epoch: 1 [12800/60000 (21%)]  Loss: 2.072088
    Train Epoch: 1 [19200/60000 (32%)]  Loss: 1.749465
    Train Epoch: 1 [25600/60000 (43%)]  Loss: 1.258822
    Train Epoch: 1 [32000/60000 (53%)]  Loss: 1.271635
    Train Epoch: 1 [38400/60000 (64%)]  Loss: 1.171696
    Train Epoch: 1 [44800/60000 (75%)]  Loss: 1.161705
    Train Epoch: 1 [51200/60000 (85%)]  Loss: 1.034610
    Train Epoch: 1 [57600/60000 (96%)]  Loss: 0.904365
    Train Epoch duration 95.98s

    Test set: Average loss: 0.0008, Accuracy: 6984/10000 (70%)

    [...]

    Train Epoch: 9 [0/60000 (0%)]   Loss: 0.813664
    Train Epoch: 9 [6400/60000 (11%)]   Loss: 0.643290
    Train Epoch: 9 [12800/60000 (21%)]  Loss: 0.792572
    Train Epoch: 9 [19200/60000 (32%)]  Loss: 0.680120
    Train Epoch: 9 [25600/60000 (43%)]  Loss: 0.951693
    Train Epoch: 9 [32000/60000 (53%)]  Loss: 0.531021
    Train Epoch: 9 [38400/60000 (64%)]  Loss: 0.510627
    Train Epoch: 9 [44800/60000 (75%)]  Loss: 0.764454
    Train Epoch: 9 [51200/60000 (85%)]  Loss: 0.707269
    Train Epoch: 9 [57600/60000 (96%)]  Loss: 0.570231
    Train Epoch duration 132.90s

    Test set: Average loss: 0.0005, Accuracy: 8193/10000 (82%)

## À ajouter

Plot en fonction des epoch:

-   training loss
-   testing loss
-   accuracy

# Fine-tuning

Les données sont disponibles à l’adresse
<https://download.pytorch.org/tutorial/hymenoptera_data.zip>

## Téléchargement des données

In [ ]:
!wget https://download.pytorch.org/tutorial/hymenoptera_data.zip
!unzip hymenoptera_data.zip

### Augmentation de données basique et très classique

In [ ]:
data_transforms = {
    # Data augmentation and normalization for training
    'train': v2.Compose([
        v2.RandomResizedCrop(224),
        v2.RandomHorizontalFlip(),
        v2.ToImage(),
        v2.ToDtype(torch.float32, scale=True),
        v2.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
    # Just normalization for validation
    'val': v2.Compose([
        v2.Resize(256),
        v2.CenterCrop(224),
        v2.ToImage(),
        v2.ToDtype(torch.float32, scale=True),
        v2.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
}

### Construction d’un dataloader

Voir <https://pytorch.org/vision/stable/datasets.html> pour les datasets
classiques et aussi
<https://pytorch.org/vision/stable/generated/torchvision.datasets.DatasetFolder.html#torchvision.datasets.DatasetFolder>
pour faire des datasets personnalisés.

In [ ]:
data_dir = 'hymenoptera_data'
image_datasets = {x: datasets.ImageFolder(os.path.join(data_dir, x),
                                          data_transforms[x])
                  for x in ['train', 'val']}
dataloaders = {x: torch.utils.data.DataLoader(image_datasets[x], batch_size=4,
                                             shuffle=True, num_workers=4)
              for x in ['train', 'val']}
dataset_sizes = {x: len(image_datasets[x]) for x in ['train', 'val']}
class_names = image_datasets['train'].classes

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [ ]:
def imshow(inp, title=None):
    """Imshow for Tensor."""
    inp = inp.numpy().transpose((1, 2, 0))
    mean = np.array([0.485, 0.456, 0.406])
    std = np.array([0.229, 0.224, 0.225])
    inp = std * inp + mean
    inp = np.clip(inp, 0, 1)
    plt.imshow(inp)
    if title is not None:
        plt.title(title)
    plt.pause(0.001)  # pause a bit so that plots are updated


# Get a batch of training data
inputs, classes = next(iter(dataloaders['train']))

# Make a grid from batch
out = torchvision.utils.make_grid(inputs)

imshow(out, title=[class_names[x] for x in classes])

## Resnet

Voir
<https://github.com/pytorch/vision/blob/master/torchvision/models/resnet.py>
pour comprendre comment couper le réseau.

In [ ]:
from torchvision.models import resnet18

model = resnet18(weights='IMAGENET1K_V1') # Modèle pré-entraîné sur ImageNet

In [ ]:
print(model)

On fixe les paramètres de toutes les couches, ils ne seront pas modifiés
lors de l’apprentissage.

In [ ]:
for param in model.parameters():
    param.requires_grad = False

On remplace la partie finale par une simple couche dense (qui sera elle
apprise).

In [ ]:
model.fc = nn.Linear(512, 2)

In [ ]:
# Calcul de la représentation, pour l'envoyer à un SVM par exemple
# model.avgpool(x) # sortie de dernièer couche avant le classifier
# Ce serait un prétraitement à appliquer à toutes les données avant d'entraîner le SVM

In [ ]:
optimizer = optim.SGD(model.fc.parameters(), lr=0.01)

criterion = nn.CrossEntropyLoss()
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
model.to(device)

ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
  

In [ ]:
for epoch in range(1, 10):
        start_time = time.process_time()
        train(model, device, dataloaders["train"], optimizer, epoch, criterion)
        end_time = time.process_time()
        print("Train Epoch duration {:.2f}s".format(end_time - start_time))
        
        test(model, device, dataloaders["val"], criterion)

Train Epoch: 1 [0/244 (0%)] Loss: 9.530968
Train Epoch duration 150.19s

Test set: Average loss: 2.7408, Accuracy: 0/153 (0%)

Train Epoch: 2 [0/244 (0%)] Loss: 9.099474

## VGG

Voir
<https://github.com/pytorch/vision/blob/master/torchvision/models/vgg.py>
et
<https://pytorch.org/docs/stable/_modules/torch/nn/modules/container.html#Sequential>